In [1]:
import numpy as np
import os
import time
import torch
import torch.nn as nn
import torch.optim as optim
import torch.nn.functional as F
import math
import random

MIN_LIST_LEN = 14
MAX_LIST_LEN = 14
MAX_STEPS = 512

SUCCESS_REWARD = 2.0
STEP_REWARD = -0.1
SWAP_REWARD = 1.0
INVALID_ACTION_REWARD = -10.0

EPS_START = 0.5
EPS_END = 0.05
EPS_DECAY = 1000
GAMMA = 0.8
NUM_EPISODES = 100000
EPISODES_SAVE = 1000
OUTPUT_DIR = 'datasets/rl_sort_transformer_easy/list14_transformer4_192_gamma08_step512_v1'

# Define the vocabulary
vocab = {
    'Comparison': 0,
    'Swap': 1,
    'less': 2,
    'equal': 3,
    'more': 4,
    '0': 5,
    '1': 6,
    '2': 7,
    '3': 8,
    '4': 9,
    '5': 10,
    '6': 11,
    '7': 12,
    '8': 13,
    '9': 14,
    '10': 15,
    '11': 16,
    '12': 17,
    '13': 18,
    '14': 19,
    '15': 20,
    'len1': 21,
    'len2': 22,
    'len3': 23,
    'len4': 24,
    'len5': 25,
    'len6': 26,
    'len7': 27,
    'len8': 28,
    'len9': 29,
    'len10': 30,
    'len11': 31,
    'len12': 32,
    'len13': 33,
    'len14': 34,
    'len15': 35,
    'len16': 36,
}
inv_vocab = {v: k for k, v in vocab.items()}

device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
print(f"Using device: {device}")

# Define the environment
class SortingEnv:
    def __init__(self):
        self.max_steps = MAX_STEPS

    def reset(self):
        self.length = random.randint(MIN_LIST_LEN, MAX_LIST_LEN)
        self.list = [random.randint(1, 100) for _ in range(self.length)]
        while self.list == sorted(self.list):
            self.list = [random.randint(1, 100) for _ in range(self.length)]
        self.indices = None
        self.current_step = 0
        self.done = False
        initial_token = 'len{}'.format(self.length)
        return vocab[initial_token], self.list.copy()
    
    def get_list(self):
        return self.list
    
    def get_list_len(self):
        return len(self.list)

    def step(self, action_tokens):
        action = action_tokens[0]
        reward = -0.01  # default penalty
        response_token = None

        if action == vocab['Comparison']:
            if len(action_tokens) != 3:
                reward = INVALID_ACTION_REWARD
                self.done = True
                return response_token, reward, self.done, self.list.copy()
            index1 = action_tokens[1] - vocab['0']
            index2 = action_tokens[2] - vocab['0']
            if index1 >= self.length or index2 >= self.length or index1 < 0 or index2 < 0:
                reward = INVALID_ACTION_REWARD
                self.done = True
                return response_token, reward, self.done, self.list.copy()
            self.indices = (index1, index2)
            if self.list[index1] < self.list[index2]:
                response_token = vocab['less']
                reward = STEP_REWARD
            elif self.list[index1] == self.list[index2]:
                response_token = vocab['equal']
                reward = STEP_REWARD * 2
            else:
                response_token = vocab['more']
                reward = STEP_REWARD
        elif action == vocab['Swap']:
            if self.indices is None:
                reward = INVALID_ACTION_REWARD
                self.done = True
                return response_token, reward, self.done, self.list.copy()
            index1, index2 = self.indices
            prev_list = self.list.copy()
            self.list[index1], self.list[index2] = self.list[index2], self.list[index1]
            if self.list == sorted(self.list):
                reward = SUCCESS_REWARD
                self.done = True
            #elif prev_list[index1] > prev_list[index2] and self.list[index1] <= self.list[index2]:
            #    reward = 0.1
            elif (index1 < index2 and prev_list[index1] > prev_list[index2] and self.list[index1] <= self.list[index2]) or \
                (index1 > index2 and prev_list[index1] < prev_list[index2] and self.list[index1] >= self.list[index2]):
                reward = SWAP_REWARD
            elif (index1 < index2 and prev_list[index1] < prev_list[index2] and self.list[index1] >= self.list[index2]) or \
                (index1 > index2 and prev_list[index1] > prev_list[index2] and self.list[index1] <= self.list[index2]):
                reward = -SWAP_REWARD
            else:
                reward = STEP_REWARD
            self.indices = None
        else:
            reward = INVALID_ACTION_REWARD
            self.done = True

        self.current_step += 1
        if self.current_step >= self.max_steps:
            self.done = True
        return response_token, reward, self.done, self.list.copy()


Using device: cuda


In [2]:
# Positional Encoding for Transformer
class PositionalEncoding(nn.Module):
    def __init__(self, d_model, max_len=512):
        super(PositionalEncoding, self).__init__()
        self.dropout = nn.Dropout(p=0.1)

        pe = torch.zeros(max_len, d_model)  # (max_len, d_model)
        position = torch.arange(0, max_len, dtype=torch.float).unsqueeze(1)  # (max_len, 1)
        div_term = torch.exp(torch.arange(0, d_model, 2).float() *
                             (-math.log(10000.0) / d_model))
        pe[:, 0::2] = torch.sin(position * div_term)  # Even indices
        pe[:, 1::2] = torch.cos(position * div_term)  # Odd indices
        pe = pe.unsqueeze(1)  # (max_len, 1, d_model)
        self.register_buffer('pe', pe)

    def forward(self, x):
        x = x + self.pe[:x.size(0)]
        return self.dropout(x)

# Transformer Model
class TransformerModel(nn.Module):
    def __init__(self, vocab_size, d_model=192, nhead=8, num_layers=4):
        super(TransformerModel, self).__init__()
        self.model_type = 'Transformer'
        self.d_model = d_model

        self.embedding = nn.Embedding(vocab_size, d_model)
        self.pos_encoder = PositionalEncoding(d_model)
        encoder_layers = nn.TransformerEncoderLayer(d_model, nhead)
        self.transformer_encoder = nn.TransformerEncoder(encoder_layers, num_layers)
        self.decoder = nn.Linear(d_model, vocab_size)

        self.init_weights()

    def init_weights(self):
        initrange = 0.1
        nn.init.uniform_(self.embedding.weight, -initrange, initrange)
        nn.init.zeros_(self.decoder.bias)
        nn.init.uniform_(self.decoder.weight, -initrange, initrange)

    def forward(self, src):
        src = self.embedding(src) * math.sqrt(self.d_model)
        src = self.pos_encoder(src)
        output = self.transformer_encoder(src)
        output = self.decoder(output)
        return output

def decode(input_tokens, inv_vocab):
    return ' '.join([inv_vocab[x] for x in input_tokens])


def save_checkpoint(model, optimizer, episode, folder, filename):
    """
    Save the model and optimizer state to the designated filepath.

    Args:
        model (nn.Module): The model to save.
        optimizer (torch.optim.Optimizer): The optimizer whose state to save.
        episode (int): The current episode number.
        filepath (str): The path where to save the checkpoint.
    """
    filepath = os.path.join(folder, filename)
    # Ensure the directory exists
    os.makedirs(os.path.dirname(filepath), exist_ok=True)
    # Save the checkpoint
    torch.save({
        'episode': episode,
        'model_state_dict': model.state_dict(),
        'optimizer_state_dict': optimizer.state_dict(),
    }, filepath)
    print(f"Checkpoint saved at episode {episode} to {filepath}")

def load_checkpoint(filepath, model, optimizer):
    """
    Load the model and optimizer state from the designated filepath.

    Args:
        filepath (str): The path from where to load the checkpoint.
        model (nn.Module): The model into which to load the state_dict.
        optimizer (torch.optim.Optimizer): The optimizer into which to load the state.

    Returns:
        int: The episode number to resume from.
    """
    if os.path.isfile(filepath):
        checkpoint = torch.load(filepath, map_location=device)
        model.load_state_dict(checkpoint['model_state_dict'])
        optimizer.load_state_dict(checkpoint['optimizer_state_dict'])
        episode = checkpoint['episode']
        print(f"Checkpoint loaded from {filepath}, resuming from episode {episode}")
        return episode
    else:
        print(f"No checkpoint found at {filepath}, starting from scratch.")
        return 0

In [ ]:
# Training Loop
def train(verbose=False):
    # Removed torch.autograd.set_detect_anomaly(True)
    vocab_size = len(vocab)
    model = TransformerModel(vocab_size).to(device)
    optimizer = optim.Adam(model.parameters(), lr=1e-4)  # Reduced learning rate
    # Optionally, load a checkpoint
    # load_checkpoint("path_to_checkpoint", model, optimizer)

    episode_cnt = 0
    total_reward = 0.0
    num_successes = 0
    total_steps = 0
    
    for episode in range(NUM_EPISODES):
        t1 = time.time()
        model.train()  # Set model to training mode
        env = SortingEnv()
        initial_token_id, current_list = env.reset()
        input_tokens = [initial_token_id]
        log_probs = []
        rewards = []
        
        state = 'expect_action'
        done = False
        success = False

        while not done and len(input_tokens) < env.max_steps:
            if verbose:
                print(decode(input_tokens, inv_vocab))
                print(env.get_list())
            # Prepare input tensor
            input_seq = torch.tensor(input_tokens, dtype=torch.long, device=device).unsqueeze(1)  # (seq_len, batch_size)
            # Get model output
            with torch.autocast(device_type=device.type, dtype=torch.bfloat16):
                output = model(input_seq)  # (seq_len, batch_size, vocab_size)
                # Get logits for the last token
                logits = output[-1, 0, :]  # (vocab_size)

                # Check for NaNs in logits
                if torch.isnan(logits).any():
                    print(f"Episode {episode}, NaNs in logits before masking.")
                    break

                # Get valid tokens based on state
                def get_valid_tokens(state):
                    action_tokens = [vocab['Comparison'], vocab['Swap']]
                    index_tokens = [vocab[str(i)] for i in range(env.length)]
                    if state == 'expect_action':
                        return action_tokens
                    elif state == 'expect_index1':
                        return index_tokens[:-1]
                    elif state == 'expect_index2':
                        return [x for x in index_tokens if x > input_tokens[-1]]
                    else:
                        # Handle unexpected states by defaulting to expect_action
                        return action_tokens

                valid_token_ids = get_valid_tokens(state)

                # Ensure valid_token_ids are within the vocab range
                if any(idx >= vocab_size or idx < 0 for idx in valid_token_ids):
                    print(f"Episode {episode}, invalid indices in valid_token_ids: {valid_token_ids}")
                    break

                # Mask invalid tokens
                mask_value = -1e9  # Use a large negative value instead of -inf
                mask = torch.full_like(logits, mask_value).to(device)
                mask[valid_token_ids] = 0
                masked_logits = logits + mask

                # Sample action. Have some chance to randomly pick a valid action.
                eps_threshold = EPS_END + (EPS_START - EPS_END) * np.exp(-1.0 * episode / EPS_DECAY)
                if random.random() < eps_threshold:
                    masked_logits = masked_logits / 4

                # Check for NaNs in masked_logits
                if torch.isnan(masked_logits).any():
                    print(f"Episode {episode}, NaNs in masked_logits after masking.")
                    break

                # Compute probabilities
                probs = F.softmax(masked_logits, dim=0)

                # Check for NaNs in probs
                if torch.isnan(probs).any():
                    print(f"Episode {episode}, NaNs in probs after softmax.")
                    break

                try:
                    m = torch.distributions.Categorical(probs)
                    action_token = m.sample()
                    log_prob = m.log_prob(action_token)
                except ValueError as e:
                    print(f"Episode {episode}, error in sampling action: {e}")
                    break

            log_probs.append(log_prob)
            input_tokens.append(action_token.item())

            action = action_token.item()
            reward = 0.0
            if state == 'expect_action':
                if action == vocab['Comparison']:
                    state = 'expect_index1'
                elif action == vocab['Swap']:
                    if env.indices is None:
                        reward = INVALID_ACTION_REWARD
                        rewards.append(reward)
                        done = True
                        continue
                    action_tokens = [vocab['Swap']]
                    response_token, reward, done, current_list = env.step(action_tokens)
                    if done and reward == SUCCESS_REWARD:
                        success = True
                    if verbose:
                        print("Reward:", reward)
                    state = 'expect_action'
                else:
                    reward = INVALID_ACTION_REWARD
                    done = True
            elif state == 'expect_index1':
                index1_token = action_token
                state = 'expect_index2'
            elif state == 'expect_index2':
                index2_token = action_token
                action_tokens = [vocab['Comparison'], index1_token.item(), index2_token.item()]
                response_token, reward, done, current_list = env.step(action_tokens)
                if done and reward == SUCCESS_REWARD:
                    success = True
                if verbose:
                    print("Reward:", reward)
                if response_token is not None:
                    input_tokens.append(response_token)
                state = 'expect_action'
            else:
                reward = INVALID_ACTION_REWARD
                done = True

            rewards.append(reward)
        #
        if success: 
            num_successes += 1
        # Save checkpoint
        if episode > 0 and episode % EPISODES_SAVE == 0:
            avg_reward = total_reward / episode_cnt
            success_rate = num_successes / episode_cnt
            avg_steps = total_steps / episode_cnt
            episode_cnt = 0
            total_reward = 0.0
            num_successes = 0
            total_steps = 0
            save_checkpoint(model, optimizer, episode, OUTPUT_DIR, f"ckpt_{episode}_{success_rate:.4f}_{avg_steps:.2f}.pth")
        #
        assert len(log_probs) == len(rewards), "log_probs and returns have different sizes!"

        if len(log_probs) == 0:
            continue  # Skip if no actions were taken

        # Compute returns and loss within autocast
        with torch.autocast(device_type=device.type, dtype=torch.bfloat16):
            # Compute returns
            returns = []
            R = 0
            gamma = GAMMA
            for r in rewards[::-1]:
                R = r + gamma * R
                returns.insert(0, R)
            returns = torch.tensor(returns).to(device)

            # Check for NaNs in returns
            if torch.isnan(returns).any():
                print(f"Episode {episode}, NaNs in returns.")
                continue

            # Compute loss
            loss = 0
            for log_prob, R in zip(log_probs, returns):
                loss -= log_prob * R

            # Check for NaNs in loss
            if torch.isnan(loss):
                print(f"Episode {episode}, NaN in loss.")
                continue

        optimizer.zero_grad()
        loss.backward()
        torch.nn.utils.clip_grad_norm_(model.parameters(), max_norm=1.0)  # Gradient clipping
        optimizer.step()

        episode_cnt += 1
        total_reward += sum(rewards)
        total_steps += len(rewards)
        t2 = time.time()
        if episode % 1 == 0:
            print(f"Episode {episode}, loss:{loss.item():.4f}, {'succeed' if success else 'fail'}, steps:{len(rewards)}, total reward:{sum(rewards):.4f}, {t2-t1} sec")

if __name__ == "__main__":
    train(verbose=False)


/home/mcwave/.local/lib/python3.10/site-packages/torch/nn/modules/transformer.py:282: UserWarning: enable_nested_tensor is True, but self.use_nested_tensor is False because encoder_layer.self_attn.batch_first was not True(use batch_first for better inference performance)
  warnings.warn(f"enable_nested_tensor is True, but self.use_nested_tensor is False because {why_not_sparsity_fast_path}")


Episode 0, loss:-92.2279, fail, steps:22, total reward:-13.6000, 0.4203352928161621 sec
Episode 1, loss:-1.9518, fail, steps:1, total reward:-10.0000, 0.005973100662231445 sec
Episode 2, loss:-5.8962, fail, steps:1, total reward:-10.0000, 0.003612995147705078 sec
Episode 3, loss:-41.4010, fail, steps:8, total reward:-9.2000, 0.019524097442626953 sec
Episode 4, loss:-10.1157, fail, steps:1, total reward:-10.0000, 0.0033807754516601562 sec
Episode 5, loss:-82.9938, fail, steps:56, total reward:-10.8000, 0.15596747398376465 sec
Episode 6, loss:-13.6514, fail, steps:1, total reward:-10.0000, 0.005990743637084961 sec
Episode 7, loss:-108.0147, fail, steps:140, total reward:-14.5000, 0.4056718349456787 sec
Episode 8, loss:-88.6918, fail, steps:36, total reward:-11.1000, 0.0979604721069336 sec
Episode 9, loss:-116.7247, fail, steps:385, total reward:-16.4000, 1.1666946411132812 sec
Episode 10, loss:-118.7235, fail, steps:386, total reward:-16.6000, 1.1191952228546143 sec
Episode 11, loss:-75.

Episode 93, loss:18.1206, fail, steps:390, total reward:7.8000, 2.244621515274048 sec
Episode 94, loss:15.0114, fail, steps:390, total reward:8.5000, 2.235929489135742 sec
Episode 95, loss:-49.2311, fail, steps:42, total reward:-6.2000, 0.26495790481567383 sec
Episode 96, loss:18.5013, fail, steps:389, total reward:7.8000, 2.1226160526275635 sec
Episode 97, loss:-69.4508, fail, steps:16, total reward:-7.4000, 0.12302803993225098 sec
Episode 98, loss:36.8774, fail, steps:390, total reward:10.9000, 2.0664472579956055 sec
Episode 99, loss:14.0535, fail, steps:390, total reward:7.8000, 2.203869581222534 sec
Episode 100, loss:19.4437, fail, steps:389, total reward:7.5000, 2.3514888286590576 sec
Episode 101, loss:-25.3542, fail, steps:145, total reward:3.8000, 0.7474081516265869 sec
Episode 102, loss:18.8374, fail, steps:389, total reward:6.5000, 2.1064374446868896 sec
Episode 103, loss:32.5863, fail, steps:390, total reward:12.9000, 2.302302360534668 sec
Episode 104, loss:47.3491, fail, ste

Episode 187, loss:87.3024, fail, steps:393, total reward:23.9000, 2.3822810649871826 sec
Episode 188, loss:114.5028, fail, steps:394, total reward:29.3000, 2.1792211532592773 sec
Episode 189, loss:-40.5652, fail, steps:1, total reward:-10.0000, 0.0491642951965332 sec
Episode 190, loss:51.7391, fail, steps:392, total reward:15.5000, 2.0606470108032227 sec
Episode 191, loss:-24.8656, fail, steps:221, total reward:2.3000, 1.1334099769592285 sec
Episode 192, loss:-33.1266, fail, steps:202, total reward:4.9000, 1.2260065078735352 sec
Episode 193, loss:67.2556, fail, steps:391, total reward:18.0000, 2.1446962356567383 sec
Episode 194, loss:73.3704, fail, steps:391, total reward:19.0000, 2.147691011428833 sec
Episode 195, loss:33.0378, fail, steps:389, total reward:9.8000, 2.1509830951690674 sec
Episode 196, loss:37.6940, fail, steps:390, total reward:12.3000, 2.109851360321045 sec
Episode 197, loss:88.7788, fail, steps:392, total reward:23.1000, 2.2659332752227783 sec
Episode 198, loss:49.47

Episode 280, loss:91.7164, fail, steps:393, total reward:24.1000, 2.239950180053711 sec
Episode 281, loss:13.6118, fail, steps:389, total reward:8.7000, 2.21001935005188 sec
Episode 282, loss:97.1006, fail, steps:393, total reward:26.2000, 2.2485287189483643 sec
Episode 283, loss:39.5395, fail, steps:390, total reward:12.9000, 2.2392473220825195 sec
Episode 284, loss:58.7707, fail, steps:391, total reward:17.6000, 2.2820327281951904 sec
Episode 285, loss:51.1235, fail, steps:391, total reward:16.0000, 2.1212821006774902 sec
Episode 286, loss:67.0170, fail, steps:392, total reward:19.8000, 2.215689182281494 sec
Episode 287, loss:84.3936, fail, steps:392, total reward:22.8000, 2.299799680709839 sec
Episode 288, loss:91.9710, fail, steps:393, total reward:24.1000, 2.006500482559204 sec
Episode 289, loss:77.5845, fail, steps:392, total reward:23.1000, 2.3443994522094727 sec
Episode 290, loss:72.1004, fail, steps:393, total reward:22.1000, 2.3745410442352295 sec
Episode 291, loss:-25.2252, 

...

Episode 55226, loss:8.4218, fail, steps:393, total reward:25.2000, 2.0875742435455322 sec
Episode 55227, loss:1.2437, fail, steps:390, total reward:11.6000, 2.2907519340515137 sec
Episode 55228, loss:2.2961, fail, steps:396, total reward:39.5000, 2.351001501083374 sec
Episode 55229, loss:3.2809, succeed, steps:338, total reward:31.7000, 2.232736587524414 sec
Episode 55230, loss:5.3358, fail, steps:394, total reward:30.3000, 2.3517277240753174 sec
Episode 55231, loss:2.1149, succeed, steps:378, total reward:28.7000, 1.9988176822662354 sec
Episode 55232, loss:5.5428, fail, steps:394, total reward:27.8000, 2.284412145614624 sec
Episode 55233, loss:15.1800, succeed, steps:328, total reward:24.6000, 1.989776372909546 sec
Episode 55234, loss:3.2097, fail, steps:390, total reward:11.1000, 2.2099483013153076 sec
Episode 55235, loss:5.2767, fail, steps:391, total reward:18.7000, 2.1734275817871094 sec
Episode 55236, loss:14.1382, succeed, steps:335, total reward:29.1000, 1.8089420795440674 sec


Episode 55317, loss:10.3842, fail, steps:393, total reward:26.1000, 2.2204174995422363 sec
Episode 55318, loss:-0.5145, fail, steps:391, total reward:16.7000, 2.303159713745117 sec
Episode 55319, loss:5.3439, fail, steps:396, total reward:37.5000, 2.2719690799713135 sec
Episode 55320, loss:5.5067, fail, steps:393, total reward:26.7000, 2.091500997543335 sec
Episode 55321, loss:0.8807, fail, steps:391, total reward:15.7000, 2.2535581588745117 sec
Episode 55322, loss:8.0195, fail, steps:395, total reward:35.4000, 2.2146291732788086 sec
Episode 55323, loss:3.5584, succeed, steps:265, total reward:14.7000, 1.5210072994232178 sec
Episode 55324, loss:2.7527, fail, steps:396, total reward:39.5000, 2.202845335006714 sec
Episode 55325, loss:4.9547, fail, steps:393, total reward:25.1000, 2.470210552215576 sec
Episode 55326, loss:3.5956, fail, steps:394, total reward:27.7000, 2.232276201248169 sec
Episode 55327, loss:2.5294, succeed, steps:260, total reward:28.2000, 1.659104824066162 sec
Episode 

Episode 55408, loss:0.7900, fail, steps:390, total reward:13.6000, 2.2121493816375732 sec
Episode 55409, loss:2.8658, fail, steps:390, total reward:14.9000, 2.2280635833740234 sec
Episode 55410, loss:6.4446, succeed, steps:332, total reward:19.5000, 1.7568199634552002 sec
Episode 55411, loss:1.3438, succeed, steps:282, total reward:9.2000, 1.5178086757659912 sec
Episode 55412, loss:3.8304, fail, steps:393, total reward:26.4000, 2.238395929336548 sec
Episode 55413, loss:3.4496, fail, steps:391, total reward:16.9000, 2.430889844894409 sec
Episode 55414, loss:3.0139, fail, steps:392, total reward:18.6000, 2.1773526668548584 sec
Episode 55415, loss:3.1037, fail, steps:391, total reward:18.0000, 2.298288106918335 sec
Episode 55416, loss:1.9845, fail, steps:389, total reward:9.8000, 2.2775304317474365 sec
Episode 55417, loss:1.6597, fail, steps:392, total reward:20.5000, 2.1894404888153076 sec
Episode 55418, loss:4.4048, fail, steps:391, total reward:17.7000, 2.2404062747955322 sec
Episode 5

Episode 55499, loss:7.7214, succeed, steps:329, total reward:29.3000, 1.9491429328918457 sec
Episode 55500, loss:5.0537, fail, steps:394, total reward:28.2000, 2.293071985244751 sec
Episode 55501, loss:6.8584, fail, steps:393, total reward:26.2000, 2.2347166538238525 sec
Episode 55502, loss:1.6073, succeed, steps:368, total reward:21.8000, 2.1174073219299316 sec
Episode 55503, loss:2.6140, fail, steps:394, total reward:28.7000, 2.2652275562286377 sec
Episode 55504, loss:4.2815, fail, steps:388, total reward:5.5000, 2.1250455379486084 sec
Episode 55505, loss:12.5086, fail, steps:394, total reward:30.3000, 2.3570635318756104 sec
Episode 55506, loss:11.4408, fail, steps:392, total reward:19.6000, 2.1180214881896973 sec
Episode 55507, loss:0.3956, fail, steps:393, total reward:23.8000, 2.231102466583252 sec
Episode 55508, loss:3.9361, fail, steps:392, total reward:23.1000, 2.372945547103882 sec
Episode 55509, loss:5.0531, fail, steps:394, total reward:28.0000, 2.3069875240325928 sec
Episod

Episode 55590, loss:1.8221, fail, steps:389, total reward:6.1000, 2.2149875164031982 sec
Episode 55591, loss:3.9632, succeed, steps:394, total reward:31.6000, 2.25219464302063 sec
Episode 55592, loss:11.5157, fail, steps:394, total reward:31.3000, 2.2399673461914062 sec
Episode 55593, loss:7.4801, fail, steps:393, total reward:26.9000, 2.2191474437713623 sec
Episode 55594, loss:7.5777, fail, steps:394, total reward:30.9000, 2.3070011138916016 sec
Episode 55595, loss:0.0437, fail, steps:393, total reward:23.6000, 2.192519426345825 sec
Episode 55596, loss:4.2713, fail, steps:394, total reward:30.2000, 2.294684648513794 sec
Episode 55597, loss:3.6572, fail, steps:395, total reward:32.3000, 2.2473855018615723 sec
Episode 55598, loss:5.6164, fail, steps:393, total reward:27.2000, 2.03416109085083 sec
Episode 55599, loss:2.4343, fail, steps:392, total reward:20.0000, 2.412095785140991 sec
Episode 55600, loss:2.9922, fail, steps:393, total reward:24.9000, 2.412315845489502 sec
Episode 55601, 